<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Middle-East-&amp;-North-Africa-" data-toc-modified-id="Middle-East-&amp;-North-Africa--1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Middle East &amp; North Africa <a class="an anchor" id="middle-east-north-africa"></a></a></span></li><li><span><a href="#North-America-" data-toc-modified-id="North-America--2"><span class="toc-item-num">2&nbsp;&nbsp;</span>North America <a class="an anchor" id="north-america"></a></a></span></li><li><span><a href="#South-America-" data-toc-modified-id="South-America--3"><span class="toc-item-num">3&nbsp;&nbsp;</span>South America <a class="an anchor" id="south-america"></a></a></span></li><li><span><a href="#Central-America-&amp;-Caribbean-" data-toc-modified-id="Central-America-&amp;-Caribbean--4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Central America &amp; Caribbean <a class="an anchor" id="central-america-caribbean"></a></a></span></li><li><span><a href="#Eastern-Europe-" data-toc-modified-id="Eastern-Europe--5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Eastern Europe <a class="an anchor" id="eastern-europe"></a></a></span></li><li><span><a href="#Western-Europe-" data-toc-modified-id="Western-Europe--6"><span class="toc-item-num">6&nbsp;&nbsp;</span>Western Europe <a class="an anchor" id="western-europe"></a></a></span></li><li><span><a href="#South-Asia-" data-toc-modified-id="South-Asia--7"><span class="toc-item-num">7&nbsp;&nbsp;</span>South Asia <a class="an anchor" id="south-asia"></a></a></span></li><li><span><a href="#Southeast-Asia-" data-toc-modified-id="Southeast-Asia--8"><span class="toc-item-num">8&nbsp;&nbsp;</span>Southeast Asia <a class="an anchor" id="southeast-asia"></a></a></span></li><li><span><a href="#Sub-Saharan-Africa-" data-toc-modified-id="Sub-Saharan-Africa--9"><span class="toc-item-num">9&nbsp;&nbsp;</span>Sub-Saharan Africa <a class="an anchor" id="sub-africa"></a></a></span></li></ul></div>

    ### Database information 
    [https://www.start.umd.edu/gtd/downloads/Codebook.pdf](https://www.start.umd.edu/gtd/downloads/Codebook.pdf)
    ### Analysis on data set 
    [https://www.kaggle.com/START-UMD/gtd#globalterrorismdb_0718dist.csv] (https://www.kaggle.com/START-UMD/gtd#globalterrorismdb_0718dist.csv)
    ### Adapted from 
    [https://wormlabcaltech.github.io/Angeles_Leighton_2016/RNASeqAnalysis.html] (https://wormlabcaltech.github.io/Angeles_Leighton_2016/RNASeqAnalysis.html)

In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
# import tissue_enrichment_analysis as tea
# import pyrnaseq_graphics as rsq
import scipy.stats as stats
import matplotlib as mpl

from IPython.core.display import HTML


# bokeh
import bokeh
# import bokeh.charts
# import bokeh.charts.utils
import bokeh.io
import bokeh.models
import bokeh.palettes
import bokeh.plotting
from bokeh.plotting import figure
from bokeh.resources import CDN
from bokeh.embed import file_html

# Display graphics in this notebook
bokeh.io.output_notebook()

Loading BokehJS ...

![](https://i.imgur.com/KavnzoT.png)

In [2]:
def make_expression_axes(tooltips, title,
                          xlabel, ylabel):
    """A function to plot the bokeh single mutant comparisons."""
    # Make the hover tool
    hover = bokeh.models.HoverTool(tooltips=tooltips,
                                   names=['circles'])

    # Create figure
    p = bokeh.plotting.figure(title=title, plot_width=650, 
                              plot_height=450)

    p.xgrid.grid_line_color = 'white'
    p.ygrid.grid_line_color = 'white'
    p.xaxis.axis_label = xlabel
    p.yaxis.axis_label = ylabel

    # Add the hover tool
    p.add_tools(hover)
    return p


def add_points(p, df1, x, y, se_x, color='blue', alpha=0.2, outline=False):
    # Define colors in a dictionary to access them with
    # the key from the pandas groupby funciton.
    df = df1.copy()
    transformed_q = -df[y].apply(np.log10)
    df['transformed_q'] = transformed_q
    #    FEATURE_delta_MEAN_IC50
    df['transform_e'] = list(np.sign(df[se_x])*df[x])
    source1 = bokeh.models.ColumnDataSource(df)

    # Specify data source
    p.circle(x='transform_e', y='transformed_q', size=7,
             alpha=alpha, source=source1,
             color=color, name='circles')
    if outline:
        p.circle(x='transform_e', y='transformed_q', size=7,
                 alpha=1,
                 source=source1, color='black',
                 fill_color=None, name='outlines')

    # prettify
    p.background_fill_color = "#DFDFE5"
    p.background_fill_alpha = 0.5
    
    return p

def selector(df,psig,fdrsig):
    """A function to separate tfs from everything else"""
    sig_p = (df['ANOVA_FEATURE_pval'] < psig)
    sig_fdr = (df['ANOVA_FEATURE_FDR'] < fdrsig)
    to_plot_yes = df[sig_p & sig_fdr]
    to_plot_not = df[~sig_p & ~sig_fdr]
    return to_plot_not, to_plot_yes

def replace_drugname(df):
    df = df.replace({'nkill':'Number People Killed',
                'nkillus':'Number US People Killed',
                'success':'Success',
                'propvalue':'Damaged Property Value',
                'nwound':'Number Wounded',
                'nwoundus':'Number US Wounded',
                'nhostkid':'Number Kidnapped Hostage',
                'nhostkidus':'Number Kidnapped US Hostage',
                'ndays':'Days Kidnapped Hostage',
                'nreleased':'Number Hostage Released',
                'ransomamt':'Ransom Amount',
                'ransomamtus':'Ransom Amount from US sources',
                'ransompaid':'Amount Ransom Paid',
                'ransompaidus':'Amount Ransom Paid by US sources'},inplace=True)

## Middle East & North Africa <a class="an anchor" id="middle-east-north-africa"></a>

In [3]:
menadf = pd.read_csv('mideastnorthaf/html_gdsc_anova/OUTPUT/results.csv')
replace_drugname(menadf)
menadf

ASSOC_ID              FEATURE  DRUG_ID  \
0            1        Assassination        3   
1            2     Eastern Province        6   
2            3        United States        6   
3            4  Target type Unknown        3   
4            5     BombingExplosion        5   
...        ...                  ...      ...   
4676      4677                Basra        6   
4677      4678         Soviet Union        4   
4678      4679             Northern        4   
4679      4680             Istanbul        4   
4680      4681             Firearms       14   

                             DRUG_NAME DRUG_TARGET  N_FEATURE_neg  \
0                              Success   Hijacking          46222   
1                    Number US Wounded   Hijacking          41793   
2                    Number US Wounded   Hijacking          41447   
3                              Success   Hijacking          48316   
4                       Number Wounded   Hijacking          17466   
...                                ...         ...            ...   
4676                 Number US Wounded   Hijacking          41543   
4677            Damaged Property Value   Hijacking          10544   
4678            Damaged Property Value   Hijacking          10490   
4679            Damaged Property Value   Hijacking          10419   
4680  Amount Ransom Paid by US sources   Hijacking             47   

      N_FEATURE_pos  FEATURE_pos_logIC50_MEAN  FEATURE_neg_logIC50_MEAN  \
0              4252                 65.263405                 89.879278   
1                 7                 16.142857                  0.016677   
2               353                  1.849858                  0.003788   
3              2158                 23.725672                 90.667688   
4             29452                  6.412026                  1.457746   
...             ...                       ...                       ...   
4676            257                  0.019455                  0.019378   
4677              4              28250.000000              27747.652821   
4678             58              27879.194655              27747.117069   
4679            129              27794.038760              27747.271364   
4680             47                 -2.106383                 -2.106383   

      FEATURE_delta_MEAN_IC50  ...  FEATURE_neg_Glass_delta  \
0                  -24.615873  ...                 0.816159   
1                   16.126180  ...                25.766891   
2                    1.846070  ...                13.057744   
3                  -66.942016  ...                 2.301301   
4                    4.954280  ...                 0.649003   
...                       ...  ...                      ...   
4676                 0.000078  ...                 0.000094   
4677               502.347179  ...                 0.000400   
4678               132.077587  ...                 0.000105   
4679                46.767396  ...                 0.000037   
4680                 0.000000  ...                 0.000000   

      FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  FEATURE_pos_IC50_sd  \
0                    0.516935         3.016062e+01            47.618922   
1                    0.393695         6.258489e-01            40.961073   
2                    0.213835         1.413774e-01             8.633155   
3                    1.573257         2.908877e+01            42.549955   
4                    0.243724         7.633681e+00            20.327378   
...                       ...                  ...                  ...   
4676                 0.000303         8.244874e-01             0.256956   
4677                 0.014995         1.256292e+06         33500.000000   
4678                 0.000759         1.259456e+06        174081.784882   
4679                 0.000315         1.263699e+06        148496.716283   
4680                 0.000000         1.444063e+01            14.440634   

      FEATURE_IC50_T_pval  ANOVA_FEATURE_

In [4]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'Middle East North Africa ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(menadf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## North America <a class="an anchor" id="north-america"></a>

In [5]:
noramdf = pd.read_csv('northam/html_gdsc_anova/OUTPUT/results.csv')
replace_drugname(noramdf)
noramdf

ASSOC_ID                                            FEATURE  DRUG_ID  \
0            1                                           Al-Qaida        1   
1            2                                           Al-Qaida        2   
2            3                                           Al-Qaida        5   
3            4                                          Hijacking        1   
4            5  Vehicle (not to include vehicle-borne explosiv...        1   
...        ...                                                ...      ...   
1632      1633                                   Incel extremists        5   
1633      1634                             Anti-Police extremists        2   
1634      1635                                            Other.1        4   
1635      1636                              Anti-White extremists        2   
1636      1637                                          Argentina        5   

                    DRUG_NAME DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  \
0        Number People Killed   Hijacking           3359              4   
1     Number US People Killed   Hijacking           2088              4   
2              Number Wounded   Hijacking           3331              4   
3        Number People Killed   Hijacking           3345             18   
4        Number People Killed   Hijacking           3344             19   
...                       ...         ...            ...            ...   
1632           Number Wounded   Hijacking           3332              3   
1633  Number US People Killed   Hijacking           2085              7   
1634   Damaged Property Value   Hijacking           1064              5   
1635  Number US People Killed   Hijacking           2086              6   
1636           Number Wounded   Hijacking           3332              3   

      FEATURE_pos_logIC50_MEAN  FEATURE_neg_logIC50_MEAN  \
0                 7.502500e+02                  0.570110   
1                 7.267500e+02                  0.297893   
2                 4.123250e+03                  1.512459   
3                 1.669444e+02                  0.571300   
4                 1.591053e+02                  0.566089   
...                        ...                       ...   
1632              6.666667e+00                  6.455882   
1633              1.714286e+00                  1.686811   
1634              1.005960e+06             995146.942763   
1635              1.666667e+00                  1.686961   
1636              6.333333e+00                  6.456182   

      FEATURE_delta_MEAN_IC50  ...  FEATURE_neg_Glass_delta  \
0                  749.679890  ...               110.759923   
1                  726.452107  ...               183.494572   
2                 4121.737541  ...               175.765864   
3                  166.373144  ...                24.529645   
4                  158.539175  ...                23.376284   
...                       ...  ...                      ...   
1632                 0.210784  ...                 0.001044   
1633                 0.027475  ...                 0.000655   
1634             10813.457237  ...                 0.000533   
1635                -0.020294  ...                 0.000484   
1636                -0.122849  ...                 0.000608   

      FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  FEATURE_pos_IC50_sd  \
0                    1.021864         6.768512e+00         7.336395e+02   
1                    1.016428         3.958984e+00         7.147108e+02   
2                    0.877594         2.345016e+01         4.696633e+03   
3                    0.373978         6.782534e+00         4.448740e+02   
4                    0.365573         6.782052e+00         4.336729e+02   
...                       ...                  ...                  ...   
1632                 0.032396         2.019714e+02         6.506407e+00   
1633                 0.021918         4.197631e+01         1.253566e+00   
1634           

In [6]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'North America ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(noramdf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## South America <a class="an anchor" id="south-america"></a>

In [7]:
souamdf = pd.read_csv('southam/html_gdsc_anova/OUTPUT/results.csv')
replace_drugname(souamdf)
souamdf

ASSOC_ID                 FEATURE  DRUG_ID                DRUG_NAME  \
0            1           Armed Assault        1     Number People Killed   
1            2                Firearms        1     Number People Killed   
2            3  Montoneros (Argentina)        2  Number US People Killed   
3            4                Military        1     Number People Killed   
4            5        BombingExplosion        1     Number People Killed   
...        ...                     ...      ...                      ...   
2279      2280                  Bogota        6        Number US Wounded   
2280      2281              Lambayeque        4   Damaged Property Value   
2281      2282                   Cesar        4   Damaged Property Value   
2282      2283                    Lara        1     Number People Killed   
2283      2284                    Beni        1     Number People Killed   

     DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  FEATURE_pos_logIC50_MEAN  \
0      Hijacking          13601           3705                  4.663158   
1      Hijacking          10784           6522                  3.378718   
2      Hijacking           3215              3                  4.000000   
3      Hijacking          15615           1691                  4.941455   
4      Hijacking           9235           8071                  0.579606   
...          ...            ...            ...                       ...   
2279   Hijacking           3050            152                  0.013158   
2280   Hijacking           3305              5             388980.200000   
2281   Hijacking           3284             26             384050.076923   
2282   Hijacking          17294             12                  1.666667   
2283   Hijacking          17303              3                  1.666667   

      FEATURE_neg_logIC50_MEAN  FEATURE_delta_MEAN_IC50  ...  \
0                     0.850820                 3.812338  ...   
1                     0.631769                 2.746949  ...   
2                     0.011198                 3.988802  ...   
3                     1.312392                 3.629063  ...   
4                     2.617325                -2.037719  ...   
...                        ...                      ...  ...   
2279                  0.013115                 0.000043  ...   
2280             382920.414977              6059.785023  ...   
2281             382920.697473              1129.379450  ...   
2282                  1.666994                -0.000328  ...   
2283                  1.666994                -0.000327  ...   

      FEATURE_neg_Glass_delta  FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  \
0                    0.971431                 0.452198         3.924455e+00   
1                    0.663718                 0.405211         4.138728e+00   
2                   26.359413                 0.655755         1.513236e-01   
3                    0.748630                 0.416943         4.847608e+00   
4                    0.336748                 0.459010         6.051165e+00   
...                       ...                      ...                  ...   
2279                 0.000137                 0.000377         3.144468e-01   
2280                 0.000611                 0.011797         9.920562e+06   
2281                 0.000113                 0.001525         9.952047e+06   
2282                 0.000060                 0.000068         5.456055e+00   
2283                 0.000060                 0.000157         5.455960e+00   

      FEATURE_pos_IC50_sd  FEATURE_IC50_T_pval  ANOVA_FEATURE_pval  \
0                8.430692         0.000000e+00        0.000000e+00   
1                6.779057        5.368998e-233       5.368998e-233   
2                6.082763        8.670018e-198       8.670018e-198   
3                8.703981        8.925036e-152       8.925036e-152   
4                4.439384        5.281257e-135       5.281257e-135   
...                   ...                 

In [9]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'South America ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(souamdf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## Central America & Caribbean <a class="an anchor" id="central-america-caribbean"></a>

In [11]:
cenamdf = pd.read_csv('cenam-carib/html_gdsc_anova/OUTPUT/results.csv')
replace_drugname(cenamdf)
cenamdf

ASSOC_ID                                      FEATURE  DRUG_ID  \
0            1                                     Military        1   
1            2                                Armed Assault        1   
2            3                                     Firearms        1   
3            4            Nicaraguan Democratic Force (FDN)        1   
4            5                                Assassination        3   
...        ...                                          ...      ...   
1408      1409                                Atlantico Sur        1   
1409      1410  Sandinista National Liberation Front (FSLN)        7   
1410      1411                                        Melee        7   
1411      1412                                        Colon        1   
1412      1413                                        Chile        5   

                     DRUG_NAME DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  \
0         Number People Killed   Hijacking           5731           2291   
1         Number People Killed   Hijacking           4801           3221   
2         Number People Killed   Hijacking           3454           4568   
3         Number People Killed   Hijacking           7512            510   
4                      Success   Hijacking           9090           1254   
...                        ...         ...            ...            ...   
1408      Number People Killed   Hijacking           8019              3   
1409  Number Kidnapped Hostage   Hijacking            818             26   
1410  Number Kidnapped Hostage   Hijacking            839              5   
1411      Number People Killed   Hijacking           8015              7   
1412            Number Wounded   Hijacking           7867              7   

      FEATURE_pos_logIC50_MEAN  FEATURE_neg_logIC50_MEAN  \
0                     8.341336                  1.674751   
1                     7.212977                  1.140387   
2                     5.732706                  0.729878   
3                    13.062745                  2.934771   
4                    87.719298                 97.678768   
...                        ...                       ...   
1408                  3.666667                  3.578626   
1409                 17.884615                 19.683374   
1410                 23.200000                 19.606675   
1411                  3.571429                  3.578665   
1412                  1.142857                  1.141858   

      FEATURE_delta_MEAN_IC50  ...  FEATURE_neg_Glass_delta  \
0                    6.666584  ...                 0.991209   
1                    6.072590  ...                 1.216957   
2                    5.002827  ...                 1.117010   
3                   10.127974  ...                 1.048000   
4                   -9.959470  ...                 0.661383   
...                       ...  ...                      ...   
1408                 0.088041  ...                 0.007569   
1409                -1.798759  ...                 0.002443   
1410                 3.593325  ...                 0.004934   
1411                -0.007236  ...                 0.000622   
1412                 0.000999  ...                 0.000225   

      FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  FEATURE_pos_IC50_sd  \
0                    0.367655             6.725712            18.132736   
1                    0.364390             4.989977            16.665096   
2                    0.343918             4.478768            14.546578   
3                    0.395134             9.664096            25.631743   
4                    0.303322            15.058554            32.834651   
...                       ...                  ...                  ...   
1408                 0.034984            11.632034             2.516611   
1409                 0.007318           736.393497           245.812177   
1410                 0.083392           728.340521            43.089442   


In [12]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'Central America & Caribbean ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(cenamdf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## Eastern Europe <a class="an anchor" id="eastern-europe"></a>

In [13]:
easteudf = pd.read_csv('easteu/html_gdsc_anova/OUTPUT/results.csv')
replace_drugname(easteudf)
easteudf

ASSOC_ID                                            FEATURE  DRUG_ID  \
0            1                                      United States        2   
1            2  Riyadus-Salikhin Reconnaissance and Sabotage B...        5   
2            3                    North Ossetia-Alania (Republic)        5   
3            4               Federation of Bosnia and Herzegovina        2   
4            5                                      Assassination        3   
...        ...                                                ...      ...   
1541      1542                                   Province Unknown       10   
1542      1543                                                NVF        5   
1543      1544                                 Serbian extremists        5   
1544      1545             Caucasus Province of the Islamic State        5   
1545      1546                                 Volgograd (Oblast)        1   

                    DRUG_NAME DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  \
0     Number US People Killed   Hijacking           4233             21   
1              Number Wounded   Hijacking           4882             10   
2              Number Wounded   Hijacking           4879             13   
3     Number US People Killed   Hijacking           4241             13   
4                     Success   Hijacking           4730            414   
...                       ...         ...            ...            ...   
1541  Number Hostage Released   Hijacking            224              6   
1542           Number Wounded   Hijacking           4888              4   
1543           Number Wounded   Hijacking           4883              9   
1544           Number Wounded   Hijacking           4875             17   
1545     Number People Killed   Hijacking           4974              4   

      FEATURE_pos_logIC50_MEAN  FEATURE_neg_logIC50_MEAN  \
0                     0.285714                  0.000945   
1                   105.200000                  2.251741   
2                    79.384615                  2.257225   
3                     0.230769                  0.001651   
4                    61.352657                 88.435518   
...                        ...                       ...   
1541                -14.666667                -14.973214   
1542                  2.500000                  2.462152   
1543                  2.444444                  2.462216   
1544                  2.470588                  2.462154   
1545                  1.500000                  1.489546   

      FEATURE_delta_MEAN_IC50  ...  FEATURE_neg_Glass_delta  \
0                    0.284769  ...                 9.267046   
1                  102.948259  ...                10.077555   
2                   77.127391  ...                 7.421825   
3                    0.229119  ...                 4.976238   
4                  -27.082861  ...                 0.846783   
...                       ...  ...                      ...   
1541                 0.306548  ...                 0.003200   
1542                 0.037848  ...                 0.002558   
1543                -0.017771  ...                 0.001200   
1544                 0.008434  ...                 0.000569   
1545                 0.010454  ...                 0.001098   

      FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  FEATURE_pos_IC50_sd  \
0                    0.507962             0.030729             0.560612   
1                    0.457930            10.215599           224.812416   
2                    0.391350            10.391971           197.080584   
3                    0.522471             0.046043             0.438529   
4                    0.555511            31.983233            48.753035   
...                       ...                  ...                  ...   
1541                 0.007415            95.781605            41.340860   
1542                 0.007570            14.796422             5.000000   
1543           

In [14]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'Eastern Europe ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(easteudf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## Western Europe <a class="an anchor" id="western-europe"></a>

In [15]:
westeudf = pd.read_csv('westeu/html_gdsc_anova/OUTPUT/results.csv')
westeudf

ASSOC_ID                                            FEATURE  DRUG_ID  \
0            1                                           Al-Qaida        5   
1            2  Popular Front for the Liberation of Palestine,...        1   
2            3                                Target type Unknown        3   
3            4                                           Al-Qaida        1   
4            5                                           Scotland        1   
...        ...                                                ...      ...   
2906      2907                                Attack type Unknown        4   
2907      2908                                             Bremen        5   
2908      2909  First of October Antifascist Resistance Group ...        1   
2909      2910                                              Libya        1   
2910      2911                         Popular Forces of April 25        3   

                   DRUG_NAME DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  \
0             Number Wounded   Hijacking          14114             15   
1       Number People Killed   Hijacking          15724              3   
2                    Success   Hijacking          16264            375   
3       Number People Killed   Hijacking          15712             15   
4       Number People Killed   Hijacking          15707             20   
...                      ...         ...            ...            ...   
2906  Damaged Property Value   Hijacking           3273             15   
2907          Number Wounded   Hijacking          14109             20   
2908    Number People Killed   Hijacking          15525            202   
2909    Number People Killed   Hijacking          15680             47   
2910                 Success   Hijacking          16592             47   

      FEATURE_pos_logIC50_MEAN  FEATURE_neg_logIC50_MEAN  \
0                 1.723333e+02              1.115701e+00   
1                 4.500000e+01              4.171330e-01   
2                 4.586667e+01              8.601205e+01   
3                 1.646667e+01              4.103233e-01   
4                 1.375000e+01              4.086713e-01   
...                        ...                       ...   
2906              1.421633e+06              1.402767e+06   
2907              1.300000e+00              1.297470e+00   
2908              4.257426e-01              4.256361e-01   
2909              4.255319e-01              4.256378e-01   
2910              8.510638e+01              8.510728e+01   

      FEATURE_delta_MEAN_IC50  ...  FEATURE_neg_Glass_delta  \
0                  171.217633  ...                20.995387   
1                   44.582867  ...                15.010524   
2                  -40.145384  ...                 1.157352   
3                   16.056343  ...                 5.441263   
4                   13.341329  ...                 6.070444   
...                       ...  ...                      ...   
2906             18866.603538  ...                 0.000371   
2907                 0.002530  ...                 0.000217   
2908                 0.000107  ...                 0.000034   
2909                -0.000106  ...                 0.000034   
2910                -0.000898  ...                 0.000025   

      FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  FEATURE_pos_IC50_sd  \
0                    0.865387         8.155012e+00         1.978508e+02   
1                    1.012463         2.970107e+00         4.403408e+01   
2                    0.804590         3.468726e+01         4.989543e+01   
3                    0.677049         2.950849e+00         2.371517e+01   
4                    0.221188         2.197752e+00         6.031660e+01   
...                       ...                  ...                  ...   
2906                 0.003666         5.091972e+07         5.145764e+06   
2907                 0.000514         1.168231e+01         4.921489e+00   
2908                 0.0001

In [16]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'Western Europe ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(westeudf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## South Asia <a class="an anchor" id="south-asia"></a>

In [17]:
soasiadf = pd.read_csv('southasia/html_gdsc_anova/OUTPUT/results.csv')
soasiadf

ASSOC_ID                                      FEATURE  DRUG_ID  \
0            1                                International        2   
1            2                          Target type Unknown        3   
2            3                                United States        2   
3            4                                     Tourists        4   
4            5                          Nationality Unknown        3   
...        ...                                          ...      ...   
3395      3396                                  Philippines        3   
3396      3397                          Nationality Unknown        7   
3397      3398                       Young Communist League        5   
3398      3399  United Peoples Democratic Solidarity (UPDS)        5   
3399      3400                                       Paktia        6   

                     DRUG_NAME DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  \
0      Number US People Killed   Hijacking          36594           1037   
1                      Success   Hijacking          42572           2402   
2      Number US People Killed   Hijacking          37495            136   
3       Damaged Property Value   Hijacking           9709              9   
4                      Success   Hijacking          44128            846   
...                        ...         ...            ...            ...   
3395                   Success   Hijacking          44966              8   
3396  Number Kidnapped Hostage   Hijacking           3671              4   
3397            Number Wounded   Hijacking          43064             18   
3398            Number Wounded   Hijacking          43075              7   
3399         Number US Wounded   Hijacking          37300            258   

      FEATURE_pos_logIC50_MEAN  FEATURE_neg_logIC50_MEAN  \
0                 4.040501e-01                  0.003197   
1                 3.825978e+01                 90.317580   
2                 6.764706e-01                  0.011842   
3                 3.888880e+07              11255.309118   
4                 5.023641e+01                 88.252357   
...                        ...                       ...   
3395              8.750000e+01                 87.537250   
3396              5.500000e+00                  5.430945   
3397              3.277778e+00                  3.281186   
3398              3.285714e+00                  3.281184   
3399              1.550388e-02                  0.015469   

      FEATURE_delta_MEAN_IC50  ...  FEATURE_neg_Glass_delta  \
0                4.008529e-01  ...                 3.043863   
1               -5.205780e+01  ...                 1.760364   
2                6.646290e-01  ...                 3.624491   
3                3.887755e+07  ...                86.625972   
4               -3.801595e+01  ...                 1.180653   
...                       ...  ...                      ...   
3395            -3.725037e-02  ...                 0.001128   
3396             6.905475e-02  ...                 0.001137   
3397            -3.408364e-03  ...                 0.000241   
3398             4.530304e-03  ...                 0.000321   
3399             3.470707e-05  ...                 0.000049   

      FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  FEATURE_pos_IC50_sd  \
0                    0.424521             0.131692         9.442485e-01   
1                    1.070878            29.572171         4.861225e+01   
2                    0.386228             0.183372         1.720820e+00   
3                    0.333236        448797.800496         1.166667e+08   
4                    0.759878            32.199079         5.002902e+01   
...                       ...                  ...                  ...   
3395                 0.001054            33.029973         3.535534e+01   
3396                 0.014835            60.721121         4.654747e+00   
3397                 0.000531            14.126405         6.424270e+00   


In [18]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'South Asia ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(soasiadf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## Southeast Asia <a class="an anchor" id="southeast-asia"></a>

In [19]:
soeastasiadf = pd.read_csv('southeastasia/html_gdsc_anova/OUTPUT/results.csv')
soeastasiadf

ASSOC_ID              FEATURE  DRUG_ID                 DRUG_NAME  \
0            1        United States        2   Number US People Killed   
1            2      Bali (Province)        2   Number US People Killed   
2            3  Target type Unknown        3                   Success   
3            4      Bali (Province)        1      Number People Killed   
4            5      Bali (Province)        6         Number US Wounded   
...        ...                  ...      ...                       ...   
2451      2452               Quezon        7  Number Kidnapped Hostage   
2452      2453            Tawi-Tawi        7  Number Kidnapped Hostage   
2453      2454          Maute Group        7  Number Kidnapped Hostage   
2454      2455                India        1      Number People Killed   
2455      2456      Lanao del Norte       10   Number Hostage Released   

     DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  FEATURE_pos_logIC50_MEAN  \
0      Hijacking           9701             60                  0.516667   
1      Hijacking           9756              5                  1.400000   
2      Hijacking          12193            292                 40.753425   
3      Hijacking          12204              5                 45.400000   
4      Hijacking           9738              3                  2.333333   
...          ...            ...            ...                       ...   
2451   Hijacking            924              4                  4.250000   
2452   Hijacking            916             12                  4.416667   
2453   Hijacking            921              7                  4.428571   
2454   Hijacking          12202              7                  1.285714   
2455   Hijacking            705             14                -12.857143   

      FEATURE_neg_logIC50_MEAN  FEATURE_delta_MEAN_IC50  ...  \
0                     0.001649                 0.515017  ...   
1                     0.004100                 1.395900  ...   
2                    90.478143               -49.724719  ...   
3                     1.262701                44.137299  ...   
4                     0.005648                 2.327685  ...   
...                        ...                      ...  ...   
2451                  4.358225                -0.108225  ...   
2452                  4.356987                 0.059680  ...   
2453                  4.357220                 0.071351  ...   
2454                  1.280774                 0.004941  ...   
2455                -12.809929                -0.047214  ...   

      FEATURE_neg_Glass_delta  FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  \
0                    6.904258                 0.761553             0.074594   
1                   16.266603                 0.716082             0.085814   
2                    1.694033                 1.010215            29.352863   
3                   11.778560                 0.865221             3.747258   
4                   14.064815                 0.575953             0.165497   
...                       ...                      ...                  ...   
2451                 0.002163                 0.018493            50.041504   
2452                 0.001187                 0.013026            50.258395   
2453                 0.001424                 0.023847            50.123559   
2454                 0.001247                 0.002311             3.961458   
2455                 0.000778                 0.000953            60.705775   

      FEATURE_pos_IC50_sd  FEATURE_IC50_T_pval  ANOVA_FEATURE_pval  \
0                0.676273         0.000000e+00        0.000000e+00   
1                1.949359        4.608504e-227       4.608504e-227   
2               49.221927        1.290535e-167       1.290535e-167   
3               51.012744        1.534945e-140       1.534945e-140   
4                4.041452        5.819303e-114       5.819303e-114   
...                   ...                  ...                 ...

In [20]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'Southeast Asia ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(soeastasiadf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)

## Sub-Saharan Africa <a class="an anchor" id="sub-africa"></a>

In [22]:
subafdf = pd.read_csv('subaf/html_gdsc_anova/OUTPUT/results.csv')
subafdf

ASSOC_ID             FEATURE  DRUG_ID                         DRUG_NAME  \
0            1       United States        2           Number US People Killed   
1            2      North Kordofan        6                 Number US Wounded   
2            3            Al-Qaida        5                    Number Wounded   
3            4            Al-Qaida        2           Number US People Killed   
4            5       Assassination        3                           Success   
...        ...                 ...      ...                               ...   
4570      4571             Katsina        1              Number People Killed   
4571      4572             Kirundo        5                    Number Wounded   
4572      4573            Benguela        7          Number Kidnapped Hostage   
4573      4574  Group name Unknown       14  Amount Ransom Paid by US sources   
4574      4575           Yei River        5                    Number Wounded   

     DRUG_TARGET  N_FEATURE_neg  N_FEATURE_pos  FEATURE_pos_logIC50_MEAN  \
0      Hijacking          13625             76                  0.644737   
1      Hijacking          13684              3                  6.333333   
2      Hijacking          14433              5                820.600000   
3      Hijacking          13696              5                  2.400000   
4      Hijacking          15900           1650                 75.151515   
...          ...            ...            ...                       ...   
4570   Hijacking          15915             22                  4.909091   
4571   Hijacking          14424             14                  3.642857   
4572   Hijacking           2229              4                  1.250000   
4573   Hijacking             92             45                 -4.400000   
4574   Hijacking          14426             12                  3.666667   

      FEATURE_neg_logIC50_MEAN  FEATURE_delta_MEAN_IC50  ...  \
0                     0.001541                 0.643196  ...   
1                     0.002265                 6.331068  ...   
2                     3.377953               817.222047  ...   
3                     0.004235                 2.395765  ...   
4                    94.572327               -19.420812  ...   
...                        ...                      ...  ...   
4570                  4.918505                -0.009414  ...   
4571                  3.660982                -0.018125  ...   
4572                  1.186631                 0.063369  ...   
4573                 -4.402174                 0.002174  ...   
4574                  3.660959                 0.005707  ...   

      FEATURE_neg_Glass_delta  FEATURE_pos_Glass_delta  FEATURE_neg_IC50_sd  \
0                    9.040089                 0.400531             0.071149   
1                   83.357986                 0.577144             0.075950   
2                   54.788919                 0.459712            14.915827   
3                   22.910549                 0.446424             0.104570   
4                    0.857166                 0.449280            22.657007   
...                       ...                      ...                  ...   
4570                 0.000507                 0.001021            18.560671   
4571                 0.000497                 0.001388            36.473710   
4572                 0.000653                 0.000925            97.054373   
4573                 0.000107                 0.000105            20.300522   
4574                 0.000156                 0.001011            36.472955   

      FEATURE_pos_IC50_sd  FEATURE_IC50_T_pval  ANOVA_FEATURE_pval  \
0                1.605856         0.000000e+00        0.000000e+00   
1               10.969655         0.000000e+00        0.000000e+00   
2             1777.682986         0.000000e+00        0.000000e+00   
3                5.366563        3.346507e-308       3.346507e-308   
4               43.226540        9.626513e-189      

In [23]:
tooltips = [('Feature', '@FEATURE'),('Label','@DRUG_NAME')]
p = make_expression_axes( tooltips, 'Sub-Saharan Africa ANOVA associations',
                         'Signed Effect Size', '-log(Q)')
to_plot_not, to_plot_yes = selector(subafdf,0.001,25)
p = add_points(p, to_plot_not, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#1a9641')
p = add_points(p, to_plot_yes, 'FEATURE_IC50_effect_size', 'ANOVA_FEATURE_pval', 'FEATURE_delta_MEAN_IC50', color='#fc8d59', alpha=0.6, outline=True)
html = file_html(p, CDN, "my plot")
HTML(html)